
## **mTurk Task Management Script MT Graf**

Emanuel Graf | 2022

### Table of Contents
* Client Configuration
* Workers Qualification
    * Block Qualification
    * Task Qualification
    * check worker with task qualification
* Qualification Requirements

* Hit Creation
* Hit Progress
* Fetch Results
* Manually Reject Assignments
* Approve all Submitted and not rejected Assignments
* Bonus for the workers
* Delete Hit


    

-----------------------------------------------------------------------------------------

### CHECKLIST BEFORE RUNNING LIVE:

#### JUPYTER NOTEBOOK

* Change create_hits_in_production
* Run Qualification 1 + 2, put qualification id in block below
* Check HIT MAX Assignment
* Check Assignment Time

#### PHP SCRIPT: 
* Comment out sandbox to go live
* copy block_qualification_id into script


In [19]:
import boto3
import xmltodict
import json

### Client configuration

In [21]:
create_hits_in_production = False # DO NOT CHANGE (SANDBOX)

environments = {
  "production": {
    "endpoint": "https://mturk-requester.us-east-1.amazonaws.com",
    "preview": "https://www.mturk.com/mturk/preview"
  },
    
  "sandbox": {
    "endpoint": 
          "https://mturk-requester-sandbox.us-east-1.amazonaws.com",
            "preview": "https://workersandbox.mturk.com/mturk/preview",
      
    
  },
}
#rodentooth (emanuel)
ACCESS_KEY ="ACCESS_KEY"
SECRET_KEY = "SECRET_KEY"

#rosni
#ACCESS_KEY ="ACCESS_KEY"
#SECRET_KEY = "SECRET_KEY"
 

mturk_environment = environments["production"] if create_hits_in_production else environments["sandbox"]
session = boto3.Session(
    aws_access_key_id=ACCESS_KEY,
    aws_secret_access_key=SECRET_KEY,
    #aws_session_token=SESSION_TOKEN
)
client = session.client(
    service_name='mturk',
    region_name='us-east-1',
    endpoint_url=mturk_environment['endpoint'],
)

print(client.get_account_balance()['AvailableBalance'])


EndpointConnectionError: Could not connect to the endpoint URL: "https://mturk-requester-sandbox.us-east-1.amazonaws.com/"

### Qualification for blocking workers. id to be used in php script

In [3]:
#https://stackoverflow.com/questions/35514931/how-to-get-qualification-type-id-when-using-boto-api-for-mturk
#qualification = Qualifications()
try: 
    qual = client.create_qualification_type(Name = 'block_qualification_10', 
                                     Description='qualification to block a worker',
                                     QualificationTypeStatus = 'Active')

    print("PUT THE QualificationTypeId IN the php script AND BELOW:") 

    print(qual["QualificationType"]["QualificationTypeId"])

except Exception as e:
    print(" change the 'Name=' of qual type if you want to create a new qualification")
    print(e)  


 change the 'Name=' of qual type if you want to create a new qualification
An error occurred (RequestError) when calling the CreateQualificationType operation: You have already created a QualificationType with this name. A QualificationType's name must be unique among all of the QualificationTypes created by the same user. (1668501616763 s)


In [4]:
# update this
block_qualification_id = "3VCXEEHJLS8KU1LL4LFH3DMOXLAX2C"

### Qualification Task (Gold Tasks)

In [5]:
import requests
#questions = open(file="Test.xml", mode="r").read()
questions = requests.get('https://datatalkturk.emanuelgraf.me/qualification_test/Test.xml').text

#answers = open(file="AnswerKey.xml", mode="r").read()
answers = requests.get('https://datatalkturk.emanuelgraf.me/qualification_test/AnswerKey.xml').text


In [6]:
#https://stackoverflow.com/questions/35514931/how-to-get-qualification-type-id-when-using-boto-api-for-mturk
#qualification = Qualifications()
try: 
    qual = client.create_qualification_type(Name = 'q1_gold_1', 
                                     Description='qualification',
                                     QualificationTypeStatus = 'Active')

    print("PUT THE QualificationTypeId IN BELOW:") 

    print(qual["QualificationType"]["QualificationTypeId"])
    print(qual)
    print(qual[0])
except Exception as e:
    print(" change the 'Name=' of qual type if you want to create a new qualification")
    print(e)  


 change the 'Name=' of qual type if you want to create a new qualification
An error occurred (RequestError) when calling the CreateQualificationType operation: You have already created a QualificationType with this name. A QualificationType's name must be unique among all of the QualificationTypes created by the same user. (1668501618117 s)


In [7]:
# update this
qualificationTypeId = "3RDXJZR9A1OMSO3X6AQPY42JBIHYCS"

In [8]:
result = client.update_qualification_type(
                     #QualificationTypeId='36GZRO2Y1D7WY5RMP45HEIT2W6AF0B',
                      QualificationTypeId=qualificationTypeId,
                      Description='This is a brief knowledge test for workers',
                      QualificationTypeStatus='Active',
                      Test=questions,
                      AnswerKey=answers,
                      TestDurationInSeconds=2400)


### Check workers that have the gold-task-hypothesis-qualification

In [9]:

response = client.list_workers_with_qualification_type(
    QualificationTypeId=qualificationTypeId,
    MaxResults=30
)
print("All the follwoing workers have the qualification survey completed:")
for idx,elem in enumerate(response["Qualifications"]):
    print("WorkerId: ",elem["WorkerId"], " Score: ",elem["IntegerValue"] ,  " Grant Time: ",str(elem["GrantTime"]))

All the follwoing workers have the qualification survey completed:
WorkerId:  A3HKGPDC0BNI6W  Score:  100  Grant Time:  2022-11-14 18:49:06+01:00


### HIT design

In [10]:
#emoji handling stuff

import pyemoji, emoji_unicode

def emoji_calback(e):
    '&#x{0};'.format(e.unicode.encode('unicode_escape').decode('utf8').lstrip('\\U0u'))



In [11]:
import urllib.parse


QUESTION_XML = """<HTMLQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2011-11-11/HTMLQuestion.xsd">
        <HTMLContent><![CDATA[{}]]></HTMLContent>
        <FrameHeight>650</FrameHeight>
        </HTMLQuestion>"""


experiments = []

info_elements = ["text", "viz"]
conv_styles = ["csmach", "csmix"]
datasets = ["ds1", "ds2"]



for ds in datasets:
    for conv_style in conv_styles:
        for info_element in info_elements:
            QUESTION_XML = """<HTMLQuestion xmlns="http://mechanicalturk.amazonaws.com/AWSMechanicalTurkDataSchemas/2011-11-11/HTMLQuestion.xsd">
        <HTMLContent><![CDATA[{}]]></HTMLContent>
        <FrameHeight>650</FrameHeight>
        </HTMLQuestion>"""
            url = 'https://datatalkturk.emanuelgraf.me/html/experiments/chatbot_%s-%s-%s.php'%(ds,conv_style,info_element)
            html_layout = requests.get(url).text
            html_layout = pyemoji.entities(html_layout)
            html_layout = emoji_unicode.replace(html_layout,emoji_calback)
            question_xml = QUESTION_XML.format(html_layout)
            experiments.append([question_xml, '%s-%s-%s'%(ds,conv_style,info_element)])



    


### Qualitfication Requirement

In [12]:
# Each of the system qualification types has an associated QualificationTypeId which can be found in the documentation for
# https://docs.aws.amazon.com/AWSMechTurk/latest/AWSMturkAPI/ApiReference_QualificationRequirementDataStructureArticle.html#ApiReference_QualificationType-IDs


task_availability_in_minutes = 60*24*7
task_completion_time_for_workers_in_minutes = 60*2



TaskAttributes = { 
    'MaxAssignments': 5,           
    # How long the task will be available on MTurk (1 hour)     
    'LifetimeInSeconds': 60*task_availability_in_minutes,
    # How long Workers have to complete each item (10 minutes)
    'AssignmentDurationInSeconds': 60*task_completion_time_for_workers_in_minutes,
    # The reward you will offer Workers for each response
    'Reward': '3.75',                              
    'Title': 'Generate hypotheses in a chat interface',
    'Keywords': 'Data Science, Hypotheses, Chatbot, Conversational',
    'Description': 'Be a data scientist! You will be chatting with a chat bot that presents you some interesting data. You will then generate relevant hypotheses about the data.',
    ## More qualification
    'QualificationRequirements': [
                {
            'QualificationTypeId': qualificationTypeId,
            'Comparator': 'GreaterThan',
            'IntegerValues': [
                80,
            ]
        },
          {
              #Worker_NumberHITsApproved
    'QualificationTypeId': '00000000000000000040',
    'Comparator': 'GreaterThan',
    'IntegerValues': [500]
  },{
              #Worker_PercentAssignmentsApproved 
    'QualificationTypeId': '000000000000000000L0',
    'Comparator': 'GreaterThan',
    'IntegerValues': [95]
  },{
              'QualificationTypeId': block_qualification_id,
              'Comparator': "DoesNotExist"
}
        
    ]
}






#Hit Description in Sandbox: (no minimum hits acceptance)

if(create_hits_in_production==False):
    TaskAttributes = { 
    'MaxAssignments': 5,           
    # How long the task will be available on MTurk (1 hour)     
    'LifetimeInSeconds': 60*task_availability_in_minutes,
    # How long Workers have to complete each item (10 minutes)
    'AssignmentDurationInSeconds': 60*task_completion_time_for_workers_in_minutes,
    # The reward you will offer Workers for each response
    'Reward': '3.75',                                      
    'Title': 'Generate hypotheses in a chat interface',
    'Keywords': 'Data Science, Hypotheses, Chatbot, Conversational',
    'Description': 'Be a data scientist! You will be chatting with a chat bot that presents you some interesting data. You will then generate relevant hypotheses about the data.',
    ## More qualification
    'QualificationRequirements': [
        {
            'QualificationTypeId': qualificationTypeId,
            'Comparator': 'GreaterThan',
            'IntegerValues': [
                80,
            ]
        },
        {
              'QualificationTypeId': block_qualification_id,
              'Comparator': "DoesNotExist"
        }
    ]
}

### Create your task

In [13]:
import re

results = []
hit_type_id = ''



#todo
print('This will create %d hits with '
     'sandbox=%s' % (len(experiments) , str(mturk_environment['endpoint'])))
print('Continue?')

s = input('(Y/N): ')
if s == 'Y' or s == 'y':


    idx = 0

    print("SAVE THE FOLLOWING:")

    for experiment_html, experiment_name   in experiments:
    
        question = experiment_html
        
        #question = experiment[0]
        response = client.create_hit(
            **TaskAttributes,
            Question = question
        )
    
        hit_type_id = response['HIT']['HITTypeId']
        results.append({
            'experiment-conditions': experiment_name,
            'hit_id': response['HIT']['HITId']
        })
    

        print("HIT "+str(idx) +" Experiment "+experiment_name +":")
        print(mturk_environment['preview']+"?groupId={}".format(hit_type_id))
        print("hit ID is:", response['HIT']['HITId'])
    
        print("------")


        idx +=1
print("------")
print("------")
print(json.dumps(results,indent=2))







    

This will create 8 hits with sandbox=https://mturk-requester-sandbox.us-east-1.amazonaws.com
Continue?
(Y/N): y
SAVE THE FOLLOWING:
HIT 0 Experiment ds1-csmach-text:
https://workersandbox.mturk.com/mturk/preview?groupId=3EXOM20K1NGYOTOS2SVWGCAP9N35PM
hit ID is: 3BKZLF990Z5X02R8JF926Y62270QYE
------
HIT 1 Experiment ds1-csmach-viz:
https://workersandbox.mturk.com/mturk/preview?groupId=3EXOM20K1NGYOTOS2SVWGCAP9N35PM
hit ID is: 37Y5RYYI0PBKDDGB6NC5IKEUIPRSXZ
------
HIT 2 Experiment ds1-csmix-text:
https://workersandbox.mturk.com/mturk/preview?groupId=3EXOM20K1NGYOTOS2SVWGCAP9N35PM
hit ID is: 3IV1AEQ4DRJ1Z9WDBLRZAK6EVX5J82
------
HIT 3 Experiment ds1-csmix-viz:
https://workersandbox.mturk.com/mturk/preview?groupId=3EXOM20K1NGYOTOS2SVWGCAP9N35PM
hit ID is: 3EKZL9T8Y8S7K6R04X4J0TMI8WMHC1
------
HIT 4 Experiment ds2-csmach-text:
https://workersandbox.mturk.com/mturk/preview?groupId=3EXOM20K1NGYOTOS2SVWGCAP9N35PM
hit ID is: 3421H3BM9AN1DEFNGDXDAG1PF3NJ9R
------
HIT 5 Experiment ds2-csmach-viz:

In [45]:
# https://workersandbox.mturk.com.

### HIT Progress

In [ ]:
#manual hit
manual = 1
if(manual):
    
    results = []
    results= [
  {
    "experiment-conditions": "ds1-csmach-text",
    "hit_id": "3BKZLF990Z5X02R8JF926Y62270QYE"
  },
  {
    "experiment-conditions": "ds1-csmach-viz",
    "hit_id": "37Y5RYYI0PBKDDGB6NC5IKEUIPRSXZ"
  },
  {
    "experiment-conditions": "ds1-csmix-text",
    "hit_id": "3IV1AEQ4DRJ1Z9WDBLRZAK6EVX5J82"
  },
  {
    "experiment-conditions": "ds1-csmix-viz",
    "hit_id": "3EKZL9T8Y8S7K6R04X4J0TMI8WMHC1"
  },
  {
    "experiment-conditions": "ds2-csmach-text",
    "hit_id": "3421H3BM9AN1DEFNGDXDAG1PF3NJ9R"
  },
  {
    "experiment-conditions": "ds2-csmach-viz",
    "hit_id": "3511RHPADVKDC4Z9DF9CHGEBPEYLRI"
  },
  {
    "experiment-conditions": "ds2-csmix-text",
    "hit_id": "371Q3BEXDHF9I8GQ750QF5U5QPPSZW"
  },
  {
    "experiment-conditions": "ds2-csmix-viz",
    "hit_id": "335HHSX8CDBHPYXE4TZUKZ40TWYHD1"
  }
]

In [122]:
import argparse
from collections import Counter
    
for idx, item in enumerate(results):
    counter = Counter()
    hit_id = item['hit_id']
    print('Checking HIT %d / %d' % (idx + 1, len(results)))
    try:
        hit = client.get_hit(HITId=hit_id)['HIT']
    except:
        print('Can\'t find hit id: %s' % (hit_id))
        continue
    total = int(hit['MaxAssignments'])
    completed = 0
    paginator = client.get_paginator('list_assignments_for_hit')
    for a_page in paginator.paginate(HITId=hit_id, PaginationConfig={'PageSize': 100}):
        for a in a_page['Assignments']:
            if a['AssignmentStatus'] in ['Submitted', 'Approved', 'Rejected']:
                completed += 1
    counter.update([(completed, total)])

    for (completed, total), count in counter.most_common():
        print('%d / %d: %d' % (completed, total, count))

Checking HIT 1 / 8
0 / 5: 1
Checking HIT 2 / 8
0 / 5: 1
Checking HIT 3 / 8
0 / 5: 1
Checking HIT 4 / 8
0 / 5: 1
Checking HIT 5 / 8
0 / 5: 1
Checking HIT 6 / 8
1 / 5: 1
Checking HIT 7 / 8
0 / 5: 1
Checking HIT 8 / 8
0 / 5: 1


### create additional assignment

In [ ]:
hit_id_for_additional_assignments = "3NCN4N1H1GNGKXL5TV7OH4U9SOBNB1"
number_of_additional_assignments = 1


print('This will add %d additional assignments to hit %s with '
     'sandbox=%s' % (number_of_additional_assignments, hit_id_for_additional_assignments , str(mturk_environment['endpoint'])))
print('Continue?')

s = input('(Y/N): ')
if s == 'Y' or s == 'y':
    
    response = client.create_additional_assignments_for_hit(
        HITId=hit_id_for_additional_assignments,
        NumberOfAdditionalAssignments=number_of_additional_assignments,
    )

### Get the results

For each item in the results array we perform the following steps:

1. Get the current status of the HIT and store it in the results array.
2. Get a list of the Assignments that have been completed for each item and store the count of Assignments completed into the results array.
3. Loop through each Assignment and capture the details of the Assignment and the results to an array of answers.
4. Approve each Assignment so that the $0.05 reward will be distributed to Workers.


In [124]:
from datetime import date
answers = []

for item in results:
    
    # Get the status of the HIT
    hit = client.get_hit(HITId=item['hit_id'])
    item['status'] = hit['HIT']['HITStatus']
    # Get a list of the Assignments that have been submitted
    assignmentsList = client.list_assignments_for_hit(
        HITId=item['hit_id'],
        AssignmentStatuses=['Submitted', 'Approved'],
        MaxResults=10
    )
    assignments = assignmentsList['Assignments']
    item['assignments_submitted_count'] = len(assignments)
    for assignment in assignments:
    
        # Retreive the attributes for each Assignment
        worker_id = assignment['WorkerId']
        assignment_id = assignment['AssignmentId']
        #print("Worker id: "+worker_id)
        
        # Retrieve the value submitted by the Worker from the XML
        answer_dict = xmltodict.parse(assignment['Answer'])
        #print(len(answer_dict['QuestionFormAnswers']))
        #print((answer_dict['QuestionFormAnswers']))
        

        if len(answer_dict['QuestionFormAnswers']) > 2:
            for answer in answer_dict['QuestionFormAnswers']['Answer']:

                print(answer['QuestionIdentifier'])
                print(answer['FreeText'])

                
            #answer = answer_dict['QuestionFormAnswers']['Answer']['FreeText']
            #answers.append(int(answer))
        elif len(answer_dict['QuestionFormAnswers']['Answer']) > 1:
            json_answers = ""
            experiment_cond = ""
            for answer in answer_dict['QuestionFormAnswers']['Answer']:

                if(answer['QuestionIdentifier']=="answers"):
                    json_answers = answer['FreeText']
                    json_answers= json.loads(json_answers)
                    
                if(answer['QuestionIdentifier']=="experiment_condition"):
                    experiment_cond= answer['FreeText']

            answers.append({"json_answers":json_answers, "experiment_cond": experiment_cond, "worker_id":worker_id, "assignment_id": assignment_id})
            print("worker_id:",worker_id, " assignment_id: ", assignment_id,  " experiment_cond:", experiment_cond)

        else:
            print(answer_dict)

        # Approve the Assignment (if it hasn't been already)
        #if assignment['AssignmentStatus'] == 'Submitted':
        #    client.approve_assignment(
        #        AssignmentId=assignment_id,
        #        OverrideRejection=False
        #    )
    print("----")

with open('result-'+str(date.today())+'.json', 'a') as fp:
    fp.write(json.dumps(answers,indent=2))
    
print("answers saved in result-"+str(date.today())+".json in jupyter notebook folder!")


----
----
----
----
----
Worker id: A3HKGPDC0BNI6W
worker_id: A3HKGPDC0BNI6W  assignment_id:  3LEIZ60CDK5UZDHKO151NUKUOWM9Z2  experiment_cond: ds2-csmach-viz
----
----
----
answers saved in result-2022-11-14.json in jupyter notebook folder!


### Rejecting Assignments

In [22]:
assignment_ids = [
    #"manually put in assignments to reject",
]


print(assignment_ids)
print('This will reject %d assignments with '
     'sandbox=%s' % (len(assignment_ids), str(mturk_environment['endpoint'])))
print('Continue?')

s = input('(Y/N): ')
if s == 'Y' or s == 'y':
    print('Rejecting assignments')
    for idx, assignment_id in enumerate(assignment_ids): 
        try:
            print(idx,assignment_id)
            print('Rejecting assignment %d / %d' % (idx + 1, len(assignment_ids)))
            client.reject_assignment(AssignmentId=assignment_id, RequesterFeedback='Invalid results')
        except:
            print("Could not reject: %s" % (assignment_id))
else:
    print('Aborting')


[]
This will reject 0 assignments with sandbox=https://mturk-requester-sandbox.us-east-1.amazonaws.com
Continue?
(Y/N): y
Rejecting assignments


### Reject all denied assignments

In [77]:
import re

approve_ids = []
reject_ids = []
store_true = False

for idx, item in enumerate(results):
    hit_id = item['hit_id']
    paginator = client.get_paginator('list_assignments_for_hit')
    try:
        for a_page in paginator.paginate(HITId=hit_id, PaginationConfig={'PageSize': 100}):
            for a in a_page['Assignments']:
                if a['AssignmentStatus'] == 'Submitted':
                    try:
                      # Try to parse the output from the assignment. If it isn't
                      # valid JSON then we reject the assignment.
                        if(answer['QuestionIdentifier']=="answers"):
                            json_answers = answer['FreeText']
                            print(len(json_answers))
                            reject_ids.append(['AssignmentId'])

                    except ValueError as e:
                        reject_ids.append(['AssignmentId'])
                else:
                    print("hit %s has already been %s" % (str(hit_id), a['AssignmentStatus']))
    except client.exceptions.RequestError:
        continue

print('This will approve %d assignments and reject %d assignments with '
     'sandbox=%s' % (len(approve_ids), len(reject_ids), str(mturk_environment['endpoint'])))
print('Continue?')

if not store_true:
    s = input('(Y/N): ')
else:
    s = 'Y'
if s == 'Y' or s == 'y':
    print('Approving assignments')
    for idx, assignment_id in enumerate(approve_ids):
        print('Approving assignment %d / %d' % (idx + 1, len(approve_ids)))
        client.approve_assignment(AssignmentId=assignment_id)
    for idx, assignment_id in enumerate(reject_ids):
        print('Rejecting assignment %d / %d' % (idx + 1, len(reject_ids)))
        client.reject_assignment(AssignmentId=assignment_id, RequesterFeedback='Invalid results')
else:
    print('Aborting')

This will approve 0 assignments and reject 0 assignments with sandbox=https://mturk-requester-sandbox.us-east-1.amazonaws.com
Continue?
(Y/N): n
Aborting


### Approve the assignments

In [131]:
import re

approve_ids = []
reject_ids = []
store_true = False

for idx, item in enumerate(results):
    hit_id = item['hit_id']
    paginator = client.get_paginator('list_assignments_for_hit')
    try:
        for a_page in paginator.paginate(HITId=hit_id, PaginationConfig={'PageSize': 100}):
            for a in a_page['Assignments']:
                if a['AssignmentStatus'] == 'Submitted':
                    try:
                      # Try to parse the output from the assignment. If it isn't
                      # valid JSON then we reject the assignment.
                        json.loads(re.search(r'<FreeText>(?P<answer>.*?)</FreeText>', a['Answer'])['answer'])
                        approve_ids.append(a['AssignmentId'])
                    except ValueError as e:
                        reject_ids.append(['AssignmentId'])
                else:
                    print("hit %s has already been %s" % (str(hit_id), a['AssignmentStatus']))
    except client.exceptions.RequestError:
        continue

print('This will approve %d assignments and reject %d assignments with '
     'sandbox=%s' % (len(approve_ids), len(reject_ids), str(mturk_environment['endpoint'])))
print('Continue?')

if not store_true:
    s = input('(Y/N): ')
else:
    s = 'Y'
if s == 'Y' or s == 'y':
    print('Approving assignments')
    for idx, assignment_id in enumerate(approve_ids):
        print('Approving assignment %d / %d' % (idx + 1, len(approve_ids)))
        client.approve_assignment(AssignmentId=assignment_id)
    for idx, assignment_id in enumerate(reject_ids):
        print('Rejecting assignment %d / %d' % (idx + 1, len(reject_ids)))
        client.reject_assignment(AssignmentId=assignment_id, RequesterFeedback='Invalid results')
else:
    print('Aborting')


hit 3J6BHNX0U9YHD0PZZ8GUTWWMZHVKNH has already been Approved
This will approve 0 assignments and reject 0 assignments with sandbox=https://mturk-requester-sandbox.us-east-1.amazonaws.com
Continue?


KeyboardInterrupt: Interrupted by user

## Bonus for the Workers

In [137]:
import re

bonus_details = [
    # "Worker ID----------------","Assignment ID----------------","amount ----------------",
    ["A3HKGPDC0BNI6W"  ,          "3LEIZ60CDK5UZDHKO151NUKUOWM9Z2", ""],
]

amount_if_not_provided = "2"



print('This will send a bonus to %d assignments '
     'sandbox=%s' % (len(bonus_details),  str(mturk_environment['endpoint'])))
print('Continue?')

if not store_true:
    s = input('(Y/N): ')
else:
    s = 'Y'
if s == 'Y' or s == 'y':
    print('Sending bonus for assignments')
    for idx, bonus_detail in enumerate(bonus_details):
        print('Sending Bonus assignment %d / %d' % (idx + 1, len(bonus_details)))
        if(bonus_detail[2] == ""):
            amount = amount_if_not_provided
        else:
            amount = bonus_detail[2]
        try:
            response = client.send_bonus(
                WorkerId=bonus_detail[0], 
                BonusAmount=amount, 
                AssignmentId=bonus_detail[1],
                Reason='Thanks for your nice work!',
                UniqueRequestToken=str(bonus_detail[0]+bonus_detail[1])
            )
        except client.exceptions.RequestError as e:
            print("this assignment already got bonussed")
        
else:
    print('Aborting')


This will send a bonus to 1 assignments sandbox=https://mturk-requester-sandbox.us-east-1.amazonaws.com
Continue?
(Y/N): y
Sending bonus for assignments
Sending Bonus assignment 1 / 1
this assignment already got bonussed


### Delete the HITs

In [18]:
from datetime import datetime

delete_all = False
hit_ids = []

if delete_all:
    for hit in client.get_all_hits():
        hit_ids.append(hit.HITId)
else:
    for item in results:
        hit_ids.append(item['hit_id'])

print('This will delete %d HITs with sandbox=%s'
         % (len(hit_ids), str(mturk_environment['endpoint'])))
print('Continue?')
s = input('(Y/N): ')
if s == 'Y' or s == 'y':
    for index, hit_id in enumerate(hit_ids):
        try:
            client.delete_hit(HITId=hit_id)
            print('disabling: %d / %d' % (index+1, len(hit_ids)))
        except:
            #print('Failed to delete: %s' % (hit_id))
            # Get HIT status
            status = client.get_hit(HITId=hit_id)['HIT']['HITStatus']
            print('HITStatus:', status)
            if status == 'Assignable':
                response = client.update_expiration_for_hit(HITId=hit_id,ExpireAt=datetime(2015, 1, 1))        
            # Delete the HIT
            try:
                client.delete_hit(HITId=hit_id)
            except:
                print('Not deleted')
            else:
                print('Deleted')
else:
    print('Aborting')

This will delete 8 HITs with sandbox=https://mturk-requester-sandbox.us-east-1.amazonaws.com
Continue?
(Y/N): y


EndpointConnectionError: Could not connect to the endpoint URL: "https://mturk-requester-sandbox.us-east-1.amazonaws.com/"